In [1]:
#%pip install xlrd openpyxl scikit-learn tqdm torchviz pandas plotly numpy nbformat tqdm

In [2]:
import pandas as pd
import sklearn as sk
import numpy as np
import torch
import torch.nn as nn
import torch.optim as optim
import torch.nn.functional as F
import pandas as pd
import tqdm as tqdm
import plotly.express as px
from torch.utils.data import DataLoader

np.version.full_version

'2.1.3'

In [3]:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
print(device.type)
torch.autocast(dtype=torch.float32, device_type=device.type).__enter__()

cuda


In [4]:
hope_production_df = pd.read_excel('data.xlsx', sheet_name="HOPE PRODUCTION")
hope_storage_df = pd.read_excel('data.xlsx', sheet_name="HOPE STORAGE AFTER COOKING")

faith_production_df = pd.read_excel('data.xlsx', sheet_name="FAITH PRODUCTION")
faith_storage_df = pd.read_excel('data.xlsx', sheet_name="FAITH STORAGE AFTER COOKING")

hope_faith_df = pd.read_excel('data.xlsx', sheet_name="HOPE-FAITH PACKAGE WEIGHTS")
hope_faith_df.rename(columns={
    x: f"Sample {i + 1}" for i, x in 
    enumerate((x for x in hope_faith_df.columns if "Unnamed" in x))}, inplace=True)

hope_faith_df.columns

Index(['PRODUCT', 'DATE OF PACKING', 'EXPIRY DATE', 'AVERAGE WEIGHT (g)',
       'Sample 1', 'Sample 2', 'Sample 3', 'Sample 4', 'Sample 5', 'Sample 6',
       'Sample 7', 'Sample 8', 'Sample 9', 'Sample 10', 'Sample 11',
       'Sample 12', 'Sample 13', 'Sample 14', 'Sample 15', 'Sample 16',
       'Sample 17', 'Sample 18', 'Sample 19', 'Sample 20', 'Sample 21',
       'Sample 22', 'Sample 23', 'Sample 24', 'Sample 25', 'Sample 26',
       'Sample 27', 'Sample 28', 'Sample 29', 'Sample 30', 'Sample 31',
       'Sample 32'],
      dtype='object')

In [47]:
hope_df = hope_storage_df.merge(hope_production_df, right_on=["BATCH no.", "PRODUCTION DATE"], left_on=["BATCH no.", "BATCH INTO STORAGE"])
faith_df = faith_storage_df.merge(faith_production_df, right_on=["BATCH no.", "PRODUCTION DATE"], left_on=["BATCH no.", "BATCH INTO STORAGE"])

hope_df["PRODUCT"] = 5409
faith_df["PRODUCT"] = 5030

def fix_columns(data: pd.DataFrame, a: str, b: str):
    aa, bb = list(data[a]), list(data[b])
    for i, (xx, yy) in enumerate(zip(aa, bb)):
        aa[i] = max(yy, xx)
        bb[i] = min(yy, xx)
    data[a] = aa
    data[b] = bb

def stddev_filter(data, col: str):
    column = data[col]
    mean = np.nanmean(column)
    std3 = 3 * (std :=np.nanstd(column))
    data[col] = data[col].map(lambda v: mean if abs(v - mean) > std3 else v)
    return data

fix_columns(hope_df, "BATCH OUT OF STORAGE", "BATCH INTO STORAGE")
fix_columns(faith_df, "BATCH OUT OF STORAGE", "BATCH INTO STORAGE")

HOPE_SHELF_LIFE = 28
FAITH_SHELF_LIFE = 30

hope_df["ESTIMATED EXPIRY"] = hope_df["BATCH INTO STORAGE"] + pd.Timedelta(days=HOPE_SHELF_LIFE)
faith_df["ESTIMATED EXPIRY"] = faith_df["BATCH INTO STORAGE"] + pd.Timedelta(days=FAITH_SHELF_LIFE)

hope_pre_df = hope_df.merge(
        hope_faith_df, left_on=["ESTIMATED EXPIRY", "PRODUCT"], right_on=["EXPIRY DATE", "PRODUCT"]
    )
faith_pre_df = faith_df.merge(
        hope_faith_df, left_on=["ESTIMATED EXPIRY", "PRODUCT"], right_on=["EXPIRY DATE", "PRODUCT"]
    )

for dddd in [hope_pre_df, faith_pre_df]:
    for col in ["BATCH WEIGHT (kg) BEFORE COOKING", "BATCH WEIGHT (kg) AFTER COOKING", "AVERAGE WEIGHT (g)"]:
        dddd = stddev_filter(dddd, col)


pre_df = pd.concat([hope_pre_df, faith_pre_df])
display(pre_df.columns)
pre_df["PRODUCT AMOUNT EXPECTED"] = [1000 * row["BATCH WEIGHT (kg) AFTER COOKING"] / row["AVERAGE WEIGHT (g)"] for _, row in pre_df.iterrows()]


ns = {}
for i, row in pre_df.iterrows():
    prod = row["PRODUCT"]
    if prod not in ns:
        ns[prod] = []
    
    for col in pre_df.columns:
        if "Sample" in col:
            if not pd.isnull(v := row[col]):
                ns[prod].append(v)

for k in ns:
    ns[k] = np.nanstd(ns[k]), np.nanmean(ns[k])

pre_df.sort_values('EXPIRY DATE')

Index(['BATCH no.', 'BATCH INTO STORAGE', 'BATCH OUT OF STORAGE',
       'BATCH WEIGHT LEAVING STORAGE (KG)', 'PRODUCTION DATE',
       'BATCH WEIGHT (kg) BEFORE COOKING', 'BATCH WEIGHT (kg) AFTER COOKING',
       'NOTES', 'PRODUCT', 'ESTIMATED EXPIRY', 'DATE OF PACKING',
       'EXPIRY DATE', 'AVERAGE WEIGHT (g)', 'Sample 1', 'Sample 2', 'Sample 3',
       'Sample 4', 'Sample 5', 'Sample 6', 'Sample 7', 'Sample 8', 'Sample 9',
       'Sample 10', 'Sample 11', 'Sample 12', 'Sample 13', 'Sample 14',
       'Sample 15', 'Sample 16', 'Sample 17', 'Sample 18', 'Sample 19',
       'Sample 20', 'Sample 21', 'Sample 22', 'Sample 23', 'Sample 24',
       'Sample 25', 'Sample 26', 'Sample 27', 'Sample 28', 'Sample 29',
       'Sample 30', 'Sample 31', 'Sample 32'],
      dtype='object')

BATCH no. BATCH INTO STORAGE BATCH OUT OF STORAGE  \
0           1637         2023-10-09           2023-10-09   
209         1823         2023-10-09           2023-10-10   
208         1823         2023-10-09           2023-10-10   
207         1823         2023-10-09           2023-10-10   
206         1822         2023-10-09           2023-10-10   
...          ...                ...                  ...   
30686       4054         2024-10-04           2024-10-07   
30687       4054         2024-10-04           2024-10-07   
30688       4055         2024-10-04           2024-10-07   
30678       4049         2024-10-04           2024-10-07   
30819       4183         2024-10-04           2024-10-06   

       BATCH WEIGHT LEAVING STORAGE (KG) PRODUCTION DATE  \
0                                  286.0      2023-10-09   
209                                262.6      2023-10-09   
208                                262.6      2023-10-09   
207                                262.6      2023-10-09   
206                                268.7      2023-10-09   
...                                  ...             ...   
30686                              270.1      2024-10-04   
30687                              270.1      2024-10-04   
30688                              258.5      2024-10-04   
30678                              274.1      2024-10-04   
30819                              168.2      2024-10-04   

       BATCH WEIGHT (kg) BEFORE COOKING  BATCH WEIGHT (kg) AFTER COOKING  \
0                            293.300000                       286.000000   
209                          265.800000                       262.600000   
208                          265.800000                       262.600000   
207                          265.800000                       262.600000   
206                          273.600000                       268.700000   
...                                 ...                              ...   
30686                        275.600000                       270.100000   
30687                        275.600000                       270.100000   
30688                        263.600000                       258.500000   
30678                        279.000000                       274.100000   
30819                        272.687148                       266.901181   

      NOTES  PRODUCT ESTIMATED EXPIRY  ... Sample 24 Sample 25  Sample 26  \
0       NaN     5030       2023-11-08  ...       586       584        582   
209     NaN     5030       2023-11-08  ...       582       583        585   
208     NaN     5030       2023-11-08  ...       585       590        590   
207     NaN     5030       2023-11-08  ...       586       584        582   
206     NaN     5030       2023-11-08  ...       582       583        585   
...     ...      ...              ...  ...       ...       ...        ...   
30686   NaN     5030       2024-11-03  ...       580       564        574   
30687   NaN     5030       2024-11-03  ...       585       585        595   
30688   NaN     5030       2024-11-03  ...       580       564        574   
30678   NaN     5030       2024-11-03  ...       580       564        574   
30819   NaN     5030       2024-11-03  ...       585       585        595   

       Sample 27  Sample 28  Sample 29  Sample 30  Sample 31  Sample 32  \
0            581        585        585        583      587.0      582.0   
209          585        583        584        587      581.0      582.0   
208          592        595        596        582      586.0      591.0   
207          581        585        585        583      587.0      582.0   
206          585        583        584        587      581.0      582.0   
...          ...        ...        ...        ...        ...        ...   
30686        575        579        581        570      578.0      588.0   
30687        589        591        588        588      584.0      587.0   
30688        575        579        581        570   

In [53]:
px.scatter_3d(pre_df, y="BATCH WEIGHT (kg) BEFORE COOKING", z="AVERAGE WEIGHT (g)", x="BATCH WEIGHT (kg) AFTER COOKING")

In [54]:
from sklearn import preprocessing

le = preprocessing.LabelEncoder()
df = pd.DataFrame()

input_amount_scaler = preprocessing.MinMaxScaler()
cooking_out__storage_in_scaler = preprocessing.MinMaxScaler()

df['product'] = le.fit_transform(pre_df['PRODUCT'])

df['time_in_storage'] = [x / np.timedelta64(1, 'D') for x in (pre_df["BATCH OUT OF STORAGE"] - pre_df["BATCH INTO STORAGE"]).values]
df['weekday'] = [x.weekday() for x in pre_df["BATCH INTO STORAGE"]]
df['weekday'] = df['weekday'] / max(df['weekday'])
df['input_amount'] = input_amount_scaler.fit_transform(pre_df["BATCH WEIGHT (kg) BEFORE COOKING"].values.reshape(-1, 1))
df['cooking_out__storage_in'] = cooking_out__storage_in_scaler.fit_transform(pre_df["BATCH WEIGHT (kg) AFTER COOKING"].values.reshape(-1, 1))
df['storage_out__packaging_in'] = preprocessing.MinMaxScaler().fit_transform(pre_df["BATCH WEIGHT LEAVING STORAGE (KG)"].values.reshape(-1, 1))
df['product_amount_expected'] = preprocessing.MinMaxScaler().fit_transform(pre_df["PRODUCT AMOUNT EXPECTED"].values.reshape(-1, 1))
df['mean'] = preprocessing.MinMaxScaler().fit_transform(pre_df["AVERAGE WEIGHT (g)"].values.reshape(-1, 1))
df['stdev'] = df["product"].map(lambda x: 0)

df.sort_values('time_in_storage')

product  time_in_storage   weekday  input_amount  \
16           1              0.0  0.500000      0.322309   
15           1              0.0  0.500000      0.293774   
14           1              0.0  0.500000      0.293774   
13           1              0.0  0.500000      0.316472   
25532        0              0.0  0.000000      0.695201   
...        ...              ...       ...           ...   
23588        0             26.0  0.333333      0.765240   
23464        0             34.0  0.166667      0.713359   
23465        0             34.0  0.166667      0.713359   
23543        0             34.0  0.166667      0.730220   
23542        0             34.0  0.166667      0.730220   

       cooking_out__storage_in  storage_out__packaging_in  \
16                    0.278580                   0.621169   
15                    0.258724                   0.610742   
14                    0.258724                   0.610742   
13                    0.258724                   0.610742   
25532                 0.690734                   0.837599   
...                        ...                        ...   
23588                 0.726835                   0.856556   
23464                 0.675692                   0.829700   
23465                 0.675692                   0.829700   
23543                 0.690734                   0.837599   
23542                 0.690734                   0.837599   

       product_amount_expected      mean  stdev  
16                    0.683944  0.031817      0  
15                    0.664694  0.013522      0  
14                    0.643500  0.031817      0  
13                    0.664694  0.013522      0  
25532                 0.519549  0.954025      0  
...                        ...       ...    ...  
23588                 0.572805  0.951002      0  
23464                 0.501185  0.950207      0  
23465                 0.524289  0.919663      0  
23543                 0.545753  0.919663      0  
23542                 0.522430  0.950207      0  

[34685 rows x 9 columns]

In [55]:
px.scatter(df, x="time_in_storage", y="storage_out__packaging_in")

In [56]:
class Data(torch.utils.data.Dataset):
    def __init__(self):
        self.data = df
        self.target = ["input_amount","cooking_out__storage_in","storage_out__packaging_in"] 
        
        x_data, y_data = [], []
        for _, row in self.data.iterrows():
            x_row, y_row = [], []
            for k, v in row.items():
                if k in self.target:
                    y_row.append(v)
                else:
                    x_row.append(v)
            x_data.append(x_row)
            y_data.append(y_row)

        self.x_tensor = torch.tensor(x_data, dtype=torch.float32, device='cuda')
        self.y_tensor = torch.tensor(y_data, dtype=torch.float32, device='cuda')
    def __len__(self) -> int:
        return len(self.data)

    def __getitem__(self, index) -> tuple[torch.Tensor, torch.Tensor]:
        return self.x_tensor[index], self.y_tensor[index]
        
torch.backends.cudnn.benchmark = True

data = Data()

def loader(data):
    return DataLoader(
        data,
        batch_size=64,
        shuffle=True
    )

In [57]:
INPUT_SIZE = len(data[0][0])
OUTPUT_SIZE = len(data[0][1])
INTERNAL = 12

class Net(nn.Module):
    def __init__(self):
            super(Net, self).__init__()
            self.l1 = nn.Linear(INPUT_SIZE, INTERNAL)
            self.lrelu = nn.LeakyReLU()
            self.l2 = nn.Linear(INTERNAL, INTERNAL)
            self.relu = nn.ReLU()
            self.l3 = nn.Linear(INTERNAL, OUTPUT_SIZE)
    
    def forward(self, x):
        return (self.l3(self.relu(self.l2((self.lrelu(self.l1(x)))))))

INPUT_SIZE, INTERNAL, INTERNAL, OUTPUT_SIZE

(6, 12, 12, 3)

In [58]:
train_dataset, test_dataset = torch.utils.data.random_split(data, [.8, .2])
train_dataset = loader(train_dataset)
display(train_dataset)
display(test_dataset)

In [59]:
model = Net().to(device)
criterion = nn.MSELoss()
optimizer = optim.Adam(model.parameters(), lr=0.0001)
scaler = torch.amp.GradScaler(device.type)
epochs = 30

In [60]:
losses = []
for i in tqdm.tqdm(range(epochs)):
    for j, (x_train, y_train) in enumerate(train_dataset):
        y_pred = model(x_train)
        cost = criterion(y_pred, y_train)
        optimizer.zero_grad(set_to_none=True)
        scaler.scale(cost).backward()
        scaler.step(optimizer)
        scaler.update()
    losses.append(r := cost.cpu().detach().numpy())
    if np.isnan(r):
        print(i)
        break
    if i % 100 == 0:
        torch.save(model, f"out/model-{i}.pt")

torch.save(model, "out/model.pt")

100%|██████████| 30/30 [00:29<00:00,  1.03it/s]


In [61]:
px.line(pd.DataFrame(dict(losses=losses)), y="losses")

In [62]:
len(test_dataset)

6937

In [65]:
model_test = torch.load('out/model.pt', map_location=torch.device(device.type))
model_test.eval()

loss2 = []
preds = []
with torch.no_grad():
    for i, (x, y) in enumerate(test_dataset):
        x = x.to(device)
        y = y.to(device)
        
        # Get predictions
        product_id = x[0]
        preds.append(abs(
            input_amount_scaler.inverse_transform(y[0].cpu().detach().numpy().reshape(1, -1)) - 
            cooking_out__storage_in_scaler.inverse_transform(y[1].cpu().detach().numpy().reshape(1, -1)))))
        y_pred = model_test(x).to(device)
        print(y_pred)
        loss = criterion(y_pred, y)
        loss2.append(loss.cpu().detach().numpy())
px.line(pd.DataFrame(dict(loss2=loss2)), y="loss2")

C:\Users\pix\AppData\Local\Temp\ipykernel_18384\4192211441.py:1: FutureWarning:

You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.



TypeError: unsupported operand type(s) for -: 'numpy.ndarray' and 'Tensor'

In [64]:
px.histogram(np.array(preds).flatten())

In [33]:
np.array(preds).mean(), np.array(preds).std()

(np.float32(7.2533193), np.float32(13.085941))

In [35]:
daaaa = abs(pre_df["BATCH WEIGHT (kg) BEFORE COOKING"] - pre_df["BATCH WEIGHT (kg) AFTER COOKING"])

In [34]:
px.histogram(daaaa)

In [36]:
np.array(daaaa).mean(), np.array(daaaa).std()

(np.float64(7.353783231083845), np.float64(13.325073963975326))